## Import Dataset

In [1]:
import pandas as pd

data_train = pd.read_csv('data/black_friday/train.csv')
print('Records in train set:', data_train.shape[0])

data_test = pd.read_csv('data/black_friday/test.csv')
print('Records in test set:', data_test.shape[0])

data_train.head()

Records in train set: 550068
Records in test set: 233599


User_ID Product_ID Gender   Age  Occupation City_Category  \
0  1000001  P00069042      F  0-17          10             A   
1  1000001  P00248942      F  0-17          10             A   
2  1000001  P00087842      F  0-17          10             A   
3  1000001  P00085442      F  0-17          10             A   
4  1000002  P00285442      M   55+          16             C   

  Stay_In_Current_City_Years  Marital_Status  Product_Category_1  \
0                          2               0                   3   
1                          2               0                   1   
2                          2               0                  12   
3                          2               0                  12   
4                         4+               0                   8   

   Product_Category_2  Product_Category_3  Purchase  
0                 NaN                 NaN      8370  
1                 6.0                14.0     15200  
2                 NaN                 NaN      1422  
3                14.0                 NaN      1057  
4                 NaN                 NaN      7969

## Data preprocessing

### Check and handle missing values

In [2]:
data_train.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 550068 entries, 0 to 550067
Data columns (total 12 columns):
User_ID                       550068 non-null int64
Product_ID                    550068 non-null object
Gender                        550068 non-null object
Age                           550068 non-null object
Occupation                    550068 non-null int64
City_Category                 550068 non-null object
Stay_In_Current_City_Years    550068 non-null object
Marital_Status                550068 non-null int64
Product_Category_1            550068 non-null int64
Product_Category_2            376430 non-null float64
Product_Category_3            166821 non-null float64
Purchase                      550068 non-null int64
dtypes: float64(2), int64(5), object(5)
memory usage: 50.4+ MB


In [3]:
data_test.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 233599 entries, 0 to 233598
Data columns (total 11 columns):
User_ID                       233599 non-null int64
Product_ID                    233599 non-null object
Gender                        233599 non-null object
Age                           233599 non-null object
Occupation                    233599 non-null int64
City_Category                 233599 non-null object
Stay_In_Current_City_Years    233599 non-null object
Marital_Status                233599 non-null int64
Product_Category_1            233599 non-null int64
Product_Category_2            161255 non-null float64
Product_Category_3            71037 non-null float64
dtypes: float64(2), int64(4), object(5)
memory usage: 19.6+ MB


* **fill the missing values in *Product_Category_2* with the mean value** of the existing values.

In [4]:
data_train['Product_Category_2'].fillna((data_train['Product_Category_2'].mean()), inplace=True)
data_test['Product_Category_2'].fillna((data_test['Product_Category_2'].mean()), inplace=True)

* **drop the *Product_Category_3* column**

In [5]:
data_train = data_train.drop(['Product_Category_3'], axis=1)
data_test = data_test.drop(['Product_Category_3'], axis=1)

### Remove unrequired columns

* *User_ID* is is the number assigned automatically to each customer and so is not useful for prediction. Therefore we remove the column from our dataset.
* *Product_ID* is not a feature of the customer. Therefore we remove the same from our dataset.

In [6]:
data_train = data_train.drop(['User_ID', 'Product_ID'], axis=1)
data_test = data_test.drop(['User_ID', 'Product_ID'], axis=1)

### Convert Categorical features to Numeric
* Convert categorical values to **one-hot encoded vectors**.

In [7]:
data_train.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 550068 entries, 0 to 550067
Data columns (total 9 columns):
Gender                        550068 non-null object
Age                           550068 non-null object
Occupation                    550068 non-null int64
City_Category                 550068 non-null object
Stay_In_Current_City_Years    550068 non-null object
Marital_Status                550068 non-null int64
Product_Category_1            550068 non-null int64
Product_Category_2            550068 non-null float64
Purchase                      550068 non-null int64
dtypes: float64(1), int64(4), object(4)
memory usage: 37.8+ MB


In [8]:
Gender_vector = pd.get_dummies(data_train['Gender'])
Age_vector = pd.get_dummies(data_train['Age'])
City_vector = pd.get_dummies(data_train['City_Category'])
Years_vector = pd.get_dummies(data_train['Stay_In_Current_City_Years'])

data_train_final = pd.concat(
    [data_train, Gender_vector,Age_vector,City_vector, Years_vector], axis=1)

Gender_vector = pd.get_dummies(data_test['Gender'])
Age_vector = pd.get_dummies(data_test['Age'])
City_vector = pd.get_dummies(data_test['City_Category'])
Years_vector = pd.get_dummies(data_test['Stay_In_Current_City_Years'])

data_test_final = pd.concat(
    [data_test, Gender_vector,Age_vector,City_vector,Years_vector], axis=1)

In [9]:
data_train_final.head()

Gender   Age  Occupation City_Category Stay_In_Current_City_Years  \
0      F  0-17          10             A                          2   
1      F  0-17          10             A                          2   
2      F  0-17          10             A                          2   
3      F  0-17          10             A                          2   
4      M   55+          16             C                         4+   

   Marital_Status  Product_Category_1  Product_Category_2  Purchase  F  ...  \
0               0                   3            9.842329      8370  1  ...   
1               0                   1            6.000000     15200  1  ...   
2               0                  12            9.842329      1422  1  ...   
3               0                  12           14.000000      1057  1  ...   
4               0                   8            9.842329      7969  0  ...   

   51-55  55+  A  B  C  0  1  2  3  4+  
0      0    0  1  0  0  0  0  1  0   0  
1      0    0  1  0  0  0  0  1  0   0  
2      0    0  1  0  0  0  0  1  0   0  
3      0    0  1  0  0  0  0  1  0   0  
4      0    1  0  0  1  0  0  0  0   1  

[5 rows x 26 columns]

### Prepare the Features and Labels

In [10]:
data_train_final.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 550068 entries, 0 to 550067
Data columns (total 26 columns):
Gender                        550068 non-null object
Age                           550068 non-null object
Occupation                    550068 non-null int64
City_Category                 550068 non-null object
Stay_In_Current_City_Years    550068 non-null object
Marital_Status                550068 non-null int64
Product_Category_1            550068 non-null int64
Product_Category_2            550068 non-null float64
Purchase                      550068 non-null int64
F                             550068 non-null uint8
M                             550068 non-null uint8
0-17                          550068 non-null uint8
18-25                         550068 non-null uint8
26-35                         550068 non-null uint8
36-45                         550068 non-null uint8
46-50                         550068 non-null uint8
51-55                         550068 non-null uint8

In [11]:
X = data_train_final[['Occupation','Marital_Status','Product_Category_1',
                           'Product_Category_2','F','M','0-17','18-25',
                            '26-35','36-45','46-50','51-55','55+','A', 
                            'B', 'C', '0', '1', '2', '3', '4+']]

y = data_train_final['Purchase']

test_data = data_test_final[['Occupation','Marital_Status','Product_Category_1',
                           'Product_Category_2','F','M','0-17','18-25',
                            '26-35','36-45','46-50','51-55','55+','A', 
                            'B', 'C', '0', '1', '2', '3', '4+']]

test_data.head()

Occupation  Marital_Status  Product_Category_1  Product_Category_2  F  M  \
0           7               1                   1                11.0  0  1   
1          17               0                   3                 5.0  0  1   
2           1               1                   5                14.0  1  0   
3           1               1                   4                 9.0  1  0   
4           1               0                   4                 5.0  1  0   

   0-17  18-25  26-35  36-45  ...  51-55  55+  A  B  C  0  1  2  3  4+  
0     0      0      0      0  ...      0    0  0  1  0  0  0  1  0   0  
1     0      0      1      0  ...      0    0  0  0  1  1  0  0  0   0  
2     0      0      0      1  ...      0    0  0  1  0  0  0  0  0   1  
3     0      0      0      1  ...      0    0  0  1  0  0  0  0  0   1  
4     0      0      1      0  ...      0    0  0  0  1  0  1  0  0   0  

[5 rows x 21 columns]

### Split data into Training and Test sets

In [12]:
from sklearn.model_selection import train_test_split

X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.4)

## Create and Train Model

In [13]:
from sklearn.linear_model import LinearRegression

model = LinearRegression()

learning = model.fit(X_train, y_train)
print('Learned model:', learning)

intercept = model.intercept_
print('Intercept parameter:', intercept)

coefficients = model.coef_
coefficients_df = pd.DataFrame(coefficients, X_train.columns, columns=['Coefficient'])
print(coefficients_df)

Learned model: LinearRegression(copy_X=True, fit_intercept=True, n_jobs=None, normalize=False)
Intercept parameter: 11986.927083120736
                    Coefficient
Occupation             5.929936
Marital_Status       -44.081913
Product_Category_1  -405.550120
Product_Category_2   -70.792795
F                   -255.369118
M                    255.369118
0-17                -540.488072
18-25               -242.616091
26-35                 -1.693194
36-45                 88.112159
46-50                 76.810703
51-55                404.433825
55+                  215.440670
A                   -308.252737
B                   -123.762439
C                    432.015176
0                    -42.223107
1                      5.640760
2                     32.755390
3                     -9.267625
4+                    13.094582


## Test the model

In [14]:
predictions = model.predict(X_test)

print('Predictions:')
for p in predictions:
    print(p)

Predictions:
12142.175086940344
8046.926661892141
10224.034479810263
10222.59897259848
7622.71970326118
8917.866529632365
10143.164272612308
7409.2910757299005
7701.216170935659
7976.461910323218
6772.094980848575
8787.889054743868
11599.238193429957
10945.736383792482
10920.442342728154
8062.875900531344
9112.042891081546
8521.748642776627
9451.766094630628
11458.966039545207
8904.709073097618
9967.126108346967
11706.660524839463
8383.634850403452
9339.526979356264
7886.981245614306
11251.909664740453
10438.169492445275
9193.112269019923
11282.881327276215
9469.974974893274
9600.712980150252
9263.812166452964
9173.633204576878
5528.047349548849
9136.416041922641
11235.832951155164
9744.490769061264
9582.649065487207
8051.016028568121
7438.9407556379565
7964.509141057335
9214.328940604999
9558.50494229963
11698.699819259884
12266.354129752717
5148.520414706727
11342.39115022949
7512.402425244012
10701.031533111158
8962.182670517752
9469.123967994265
10260.799658938264
9413.41352556212


9189.330314673478
9220.928259724038
12172.941847363782
7726.210691186876
6925.88707049188
11435.759759384659
8360.7818300451
9679.828080204941
8948.049745300099
5704.006461814052
8330.728152704209
9108.836430789162
11789.385569017484
8334.335081526648
10551.375893786655
6531.312056226751
9275.858957168068
10646.46133887593
10622.817247033234
9832.942059681092
9257.572231659446
9332.369914727184
9388.824493193419
6176.642054799468
10845.653553091473
9454.264165170174
5574.973373635841
9474.246832315526
10238.660802687618
10844.01401294966
10784.31762654624
9006.374298627336
10152.273474544643
9873.880080551628
10393.75422266158
10018.06276381362
8297.378047634405
9016.07322765487
10884.638289857592
10761.07403500544
11581.2755553833
8712.947868618088
7237.476151447036
12233.097521022222
11438.2948089007
9302.423477585222
11387.806807765872
9961.826578144006
11566.963995133203
11988.474199525599
6656.365069252104
7788.950484469421
8003.179855068763
12106.979110501552
8378.623411114448
79

11202.681042290753
9830.334743699632
12671.103731496509
9168.069705638902
8595.774790398365
7971.565046972779
11516.355321388952
6376.895817042061
7766.407944428074
4797.65446626616
7102.591888451295
11900.897099319698
9124.819799075702
10472.591476821473
10622.817247033234
7554.6727134350685
10994.937465700203
9404.852137104088
9725.861020393428
10476.47892546532
8839.624694679258
11234.53664605147
6991.778649213531
10870.834242402856
11829.737489375295
12172.941847363782
8371.77497844023
10285.481833807167
4878.475664135009
7368.731062245778
9084.855915772067
11748.170076710741
8945.496065004385
10221.213844819216
5345.973636564227
10913.370385564138
9215.916820435035
10096.996236430525
7663.064194149695
8254.331317031034
10351.367073370828
9480.718536529592
8565.307253955325
7845.136133432885
10898.510854921691
10933.385698579055
7679.387499587189
9479.826208444018
10228.420161899829
12214.964863000956
7428.563957821567
8983.932128606406
6607.744360503786
3533.1909023185
7956.982845

8685.255455107277
8187.438344418235
10584.66127610327
9184.559659679177
11300.98579914017
11704.000973667211
6992.731687954975
8654.074286434683
11659.081537365271
8849.494170939332
10584.246493101886
9442.171936542683
11413.035776709132
11405.157575585015
8824.96047961406
5795.364785694042
12507.909635330814
11620.212746358282
2773.276551196106
7837.739582332643
8910.521864267927
9602.905179589863
9142.133454634892
8478.855258109941
9161.581354116792
11384.574180188562
9800.011635103154
10711.608830523319
9233.688495847577
8569.383750942336
10630.87216511162
8878.248050339062
9464.016557581926
10455.992380417623
7512.402425244012
11292.661550111943
11196.751106309142
10803.31085359808
9523.65876747447
8210.647322248153
10496.222942740631
9143.846213784804
10913.370385564138
9018.850466843764
10000.133363340337
5404.571094163695
8570.474114889028
4936.194499091983
10690.561528486995
9469.398074712477
9465.423763704097
9061.197874745889
11464.895975526817
12220.928587255625
7797.4527813

8101.846879779381
8761.63426130138
6789.285804424594
7814.059980110279
10888.429960329853
12226.002209394908
6961.006298979895
9988.941208536018
11715.302430089934
8931.993639563025
4209.1758579026355
11749.270773861987
11092.675051922826
9196.32460670083
10899.10121105445
8950.026075322163
10416.89213109281
11217.374596061572
8760.245334750083
8557.10648296396
6627.956321168478
8987.27042261236
9978.265630151414
10273.209012504205
9541.952063207593
9617.950640838422
9583.606530394754
8085.773118888516
10706.240099199678
9693.182544696749
10138.426679774646
9352.172492958352
9160.358603230829
8534.454536393252
11150.588850987488
12123.611286932917
9921.427412395358
9716.602527801333
11384.501005805068
7266.649678969447
7709.272681194367
8193.174249481446
12593.977252355311
8249.641888463393
7370.413087348724
8234.259422091594
7794.863059607477
10531.609943354655
10889.808097871777
10400.330447105092
11185.229398391595
11126.904062146206
9075.305715340457
10218.341705704275
11296.645051

...

9490.308662404666
11207.315849907303
4701.92046064041
7431.122265040593
7748.065140963224
4716.419127489002
11455.142537943366
10704.960126479398
8728.863372663998
9803.922785551686
11357.419292733699
7379.465489342323
7722.897089725486
11125.347128366753
5683.305300535004
10936.780585044624
8187.244313499836
10965.3250971724
7581.821132100139
10345.224457820126
8749.260925572262
9540.248244688435
9671.578152365051
4493.442666940798
4544.7575384796755
11375.55979856935
5338.182129154364
7771.996822769022
5275.063503611553
8805.716174068955
7839.311409418687
11278.51239306689
9151.5030267451
8388.540299379914
9130.089808428473
5354.323412522466
9169.0005084813
7922.560861503975
8192.584553788602
7617.141543458642
7983.805632476304
8646.370037256807
10189.784514548439
8733.978919674211
9964.753547844542
9398.849412792832
6055.468235643427
11178.651212711753
11590.794408748878
11964.468290280949
10299.627584561802
9311.676033566984
8109.747727025897
8686.655763795348
6991.681939120026
822

9771.738056127588
6234.164929769033
8278.186217915441
8653.493218631585
8193.174249481446
8137.232464750649
7667.5276276239665
9676.043506550788
9924.617938582474
10069.126630470979
8303.307983616018
7501.915059776294
10764.152441317934
10281.011323243563
9397.96473621493
8861.428486246907
8616.141732751299
11397.498376069332
9499.10512986079
9467.966336480795
10667.918283508625
7174.785428272551
9725.743682176455
11218.792114561873
7808.863357885798
9118.978817629535
9823.171585957853
9060.683573865548
10195.40008627333
8652.154924646176
11179.582104620991
9743.993019956924
9763.65382848595
6657.121404944047
6852.411374080047
9591.082619006893
10453.431340567584
11407.955034760602
9055.111310922439
11560.437234156525
7817.947190947151
10401.809140739964
10625.756044973165
11426.29223422357
9082.879431910618
9952.70796566829
10043.022872185009
10191.247976899878
9562.286896646077
8484.268411773024
11404.239078892408
9177.9370943676
8257.355070264248
7847.0035064323665
7889.862668313978

11768.841307355247
8210.964057426281
8892.96219029994
9550.985440223352
12199.747415952419
8551.314389856789
11174.058199727233
7811.447477509902
9697.513150937637
9508.710149042457
10964.956531451206
7637.361617067469
9592.569193508014
10303.503206256808
8739.481192784107
8588.068599497363
4522.7329994987385
9234.571508428364
11517.707824994272
9707.647078076174
9774.48519327456
9411.327691905975
9270.523418011042
7519.130408925655
11512.205984856564
10114.216876373779
8515.441977562456
8601.188395731535
8513.91809168108
7639.896666583512
7676.6025908615775
10504.970973859909
12047.52446051505
9277.072489613045
9188.215405669484
6227.336931759043
11719.218420715748
9068.678541349753
7886.981245614306
7457.399708998774
10318.438352750221
7225.045543530878
11518.778863127214
9496.238598386277
8547.848232501121
9795.589459083389
5265.343092645951
7186.154486985571
10735.585903923278
10550.519579944328
5572.43365508551
8823.848832090222
11178.656520120943
10748.113347925546
10085.05725594

8177.691840379294
10143.164272612308
9517.823629127051
7174.294477027081
8933.934373744542
7985.255107785654
7549.7758500846285
11058.004005674895
8257.2459137657
8187.438344418235
5912.09821117617
9962.98657650988
4262.633644020795
8752.735216486908
9528.505896909759
9222.230323943237
11882.116758577438
6314.6343231309875
12298.840280585842
8250.896024689064
11775.89191315515
9597.012554988505
8893.796979346069
3362.974956153561
11633.596504202878
9223.187788850784
8089.109237698761
8129.6628704834975
4087.624421451912
2817.1561973695243
7034.665619087385
8466.478603828193
11537.424984914378
10641.407063651532
10864.423680016718
9801.288867634388
11763.093464194744
9220.928259724038
11414.39331352743
10101.055736372215
11409.324951848008
8996.271285452622
8823.848832090222
7829.752141360986
10513.453698366186
9446.226749637091
9929.11372408945
11034.61332836754
8181.314377518224
5549.455345581185
11221.705598318278
5925.4192216535985
9243.78731204665
11599.976639495831
11095.850101214

8065.448261427639
8379.374459201768
11190.858481707784
9229.40330272179
8979.66341665921
8339.743913348013
10646.379534725595
7618.715495280306
8325.311680488494
9763.976713606
11331.11163143387
11749.164852998541
9507.971576773281
10578.577878031576
7961.878213935641
5327.916436387373
11223.426922178422
12229.397095860475
10085.057255940144
9471.605318783186
10212.089529092056
10514.9253031901
10331.56321515924
10646.060838574036
9267.061414526237
8585.533899004018
10988.348883070172
10900.100421016357
10326.356314391447
10072.148908962
10396.774075245092
10012.660952462464
5768.479432633521
9475.485838557073
9619.617338638238
10763.302021387963
9204.495988597502
7749.902563618952
10593.753769853
4368.593741365021
12041.594524533439
11094.20586895621
9188.065437436397
8259.899835906108
10643.165705011941
10115.85714889738
8195.450581821719
8875.659739751994
11207.782160190367
11057.637114265313
9127.351348237458
7639.896666583512
11698.195539341808
10400.01751565931
9506.227469765307


## Evaluate the model

In [15]:
from sklearn import metrics

mae = metrics.mean_absolute_error(y_test, predictions)
print('MAE:', mae)

mse = metrics.mean_squared_error(y_test, predictions)
print('MSE:', mse)

MAE: 3588.1242758298577
MSE: 21952900.143632695


## Make Predictions

In [16]:
money_spent = model.predict(test_data)
money_df = pd.DataFrame(money_spent, columns=['Money Spent'])

cols = ['Occupation','Marital_Status','Product_Category_1',
        'Product_Category_2','F','M','0-17','18-25','26-35','36-45',
        '46-50','51-55','55+','A','B','C','0','1','2','3','4+']

col_names = ['Occupation','Marital_Status','Female','Male','Age 0-17',
        'Age 18-25','Age 26-35','Age 36-45','Age 46-50','Age 51-55','Age 55+',
        'City A','City B','City C', 'Yrs 0', 'Yrs 1', 'Yrs 2', 'Yrs 3', 'Yrs 4+']

df = pd.concat([test_data, money_df], axis=1)

display(df.head())

Occupation  Marital_Status  Product_Category_1  Product_Category_2  F  M  \
0           7               1                   1                11.0  0  1   
1          17               0                   3                 5.0  0  1   
2           1               1                   5                14.0  1  0   
3           1               1                   4                 9.0  1  0   
4           1               0                   4                 5.0  1  0   

   0-17  18-25  26-35  36-45  ...  55+  A  B  C  0  1  2  3  4+   Money Spent  
0     0      0      0      0  ...    0  0  1  0  0  0  1  0   0  11041.256633  
1     0      0      1      0  ...    0  0  0  1  1  0  0  0   0  11160.589655  
2     0      0      0      1  ...    0  0  1  0  0  0  0  0   1   8652.000566  
3     0      0      0      1  ...    0  0  1  0  0  0  0  0   1   9411.514660  
4     0      0      1      0  ...    0  0  0  1  0  1  0  0   0  10197.286190  

[5 rows x 22 columns]